# Analyse der Straftaten in Los Angeles während der vergangenen Jahre

### finales Projekt zur Datenvisualisierung

### vorgelegt von Samuel Bäuerle | DHBW Heilbronn | Kurs WI23A2 | 2. Theoriesemester

Die Stadt Los Angeles im US-Bundesstaat Kalifornien ist bekannt für ihre beeindruckende Skyline, ihre kulturelle Vielfalt und nicht zuletzt für ihren Stadtteil Hollywood, in dem viele bekannte Filmstudios wie beispielsweise Universal, Warner Bros., Paramount Pictures und Sony Pictures ihre Blockbuster produzieren. Allerdings steht die Stadt Los Angeles auch im Fokus einer Debatte über urbane Kriminalität und Sicherheit. So berichtete die Bürgermeisterin von Los Angeles im Januar 2024 beispielsweise darüber, dass sich viele Menschen in der Stadt nicht sicher fühlen würden und die Stadt mit einer Serie von Blitzraubüberfällen zu kämpfen habe. Aus diesem Grund befasst sich diese Datenvisualisierung mit der Entwicklung der Straftaten in Los Angeles während der vergangenen Jahre. So soll beispielsweise überprüft werden, inwiefern sich die Anzahl der Straftaten monatlich veränderte, an welchen Tagen besonders viele Straftaten auftraten, an welchen Orten und Bezirken in Los Angeles besonders viel Kriminalität vorherrschte, zu welcher Uhrzeit die meisten Straftaten auftraten und es wird analysiert, welches Alter und welche Herkunft die häufigsten Opfer von Kriminalität sind. Darüber hinaus soll ermittelt werden, welche Arten von Straftaten am häufigsten auftreten und welche Art von Waffen bei der Durchführung der Straftaten verwendet wird.

In [6]:
!pip install pandas
!pip install plotly==5.21.0

In [7]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


## Datenverarbeitung:

In [8]:
# Importe der für die Datenanalyse benötigten Bibliotheken
import pandas as pd
import plotly.express as px
import plotly.io as pio

In [25]:
pio.renderers.default = "colab"

In [42]:
# Einlesen des Datensatzes
df = pd.read_csv('/content/data.csv')
df.to_csv('/content/drive/MyDrive/assets/data.csv')
# Der Datensatz, der für diese Datenanalyse ausgewählt wurde, stammt von Kaggle. Er bietet Einblicke in Straftaten in Los Angeles aus den vergangenen Jahren. Die Daten stammen aus Original-Strafberichten des Los Angeles Police Department.

In [39]:
# Übernahme der für die Datenauswertung relevanten Spalten des Pandas-Dataframe
df_cln = pd.DataFrame({
    "date_rptd": df['Date Rptd'],
    "date_occurance": df['DATE OCC'],
    "time_occurance": df['TIME OCC'],
    "area": df['AREA'],
    "area_name": df['AREA NAME'],
    "crm_code_desc": df['Crm Cd Desc'],
    "victim_age": df['Vict Age'],
    "victim_sex": df['Vict Sex'],
    "victim_descent": df['Vict Descent'],
    "weapon_desc": df["Weapon Desc"],
    "LAT": df['LAT'], "LON": df['LON']
})

# Erklärung der Relvanz der einzelnen Spalten:

# - DR_NO: irrelevant
# - **Date Rptd: Datum, an dem die Straftat Protokolliert wurde; relevant**
# - **DATE OCC: Datum, an dem die Straftat aufgetreten ist; relevant**
# - **TIME OCC: Uhrzeit, an der die Straftat begangen worden ist; relevant**
# - **AREA: Region; relevant**
# - **AREA NAME: jeder Nummer von "Area" lässt sich ein Name zuordnen, relevant**
# - Rpt Dist No: stellt eine Nummer von Unterbezirken im jeweiligen Gebiet dar, später u.U. relevant, jetzt erst mal irrelevant
# - Part 1-2: Aufteilung in 2 verschiedene Bereiche, irrelevant
# - Crm Cd: Gibt an, was für eine Straftat begangen worden ist (Code); irrelevant
# - **Crm Cd Desc: jeder Nummer von Crm Cd wird eine Straftat zugeordnet; relevant**
# - Mocodes: beschreibt anhand einiger Codes den Tathergang des Täters => "Modus Operandi"; erst mal irrelevant
# - **Vict Age: Alter des Opfers; relevant**
# - **Vict Sex: Geschlecht des Opfers; relevant**
# - **Vict Descent: Herkunft des Opfers; relevant**
# - Premis Cd: Nummer mit der Beschreibung der Ortes; erst mal irrelevant
# - Premis Desc: Beschreibung des Ortes; erst mal irrelevant
# - Premis Desc Cd: Ordnet jeder Nummer einen Ort zu; erst mal irrelevant
# - Weapon Used Cd: Nummer mit der jeweiligen Waffe; irrelevant
# - **Weapon Desc: Beschreibung der jeweiligen Waffe; relevant**
# - Status Desc: Beschreibt den Status, sagt aber relativ wenig aus; irrelevant
# - Crm Cd 1-4: falls noch andere mehrere Straftaten aufgetreten sind, stehen sie hier drin, ist aber größtenteils leer; irrelevant
# - LOCATION: Beschreibung des Ortes; erst mal irrelevant
# - **LAT: Längengrad; relevant - für Grafik des Ortes**
# - **LON: Breitengrad; relevant - für Grafik des Ortes**

In [22]:
# Überprüfung des Datumstyps, ggf. Konvertierung
if not pd.api.types.is_datetime64_any_dtype(df_cln['date_occurance']):
    df_cln['date_occurance'] = pd.to_datetime(df_cln['date_occurance'], format='%m/%d/%Y %I:%M:%S %p')

# Extraktion des Datums
if df_cln['date_occurance'].dt.time.any():
    df_cln['date_occurance'] = df_cln['date_occurance'].dt.date

## Verlauf der Straftaten über die Zeit, Monatsansicht
Zunächst soll analysiert werden, inwieweit sich die Anzahl der Straftaten während der vergangenen Jahre in Los Angeles langfristig entwickelt hat. Das Diagramm zeigt, wie sich die Anzahl der Straftaten über die Monate hinweg entwickelt hat. Insgesamt lässt sich beobachten, dass die Anzahl der Straftaten im Frühjahr leicht abnimmt und dann im Sommer wieder leicht ansteigt. Insgesamt bleibt die Anzahl der Straftaten recht konstant.


In [38]:
# Sicherstellen, dass 'date_occurance' im richtigen Format ist
df_cln['date_occurance'] = pd.to_datetime(df_cln['date_occurance'])

# Erstellen einer neuen Spalte 'year_month' zur Aggregation der Daten nach Monat und Jahr
df_cln['year_month'] = df_cln['date_occurance'].dt.to_period('M')

# Kovertierung von 'year_month' zu einem String => Kompatibilität mit Plotly
df_cln['year_month'] = df_cln['year_month'].astype(str)

# Aggregieren der Daten, um die Anzahl der Straftaten pro Monat zu zählen
monthly_crimes = df_cln.groupby('year_month').size().reset_index(name='counts')
# Erstellen eines Säulendiagramms
fig = px.bar(monthly_crimes, x='year_month', y='counts',
             title='Monatliche Entwicklung der Straftaten in Los Angeles',
             labels={'year_month': 'Monat', 'counts': 'Anzahl der Straftaten'},
             template='plotly_white')  # Nutzt ein helles Thema, passend für eine weiße Website

# Anpassen des Layouts
fig.update_layout(
    xaxis_title='Monat und Jahr',
    yaxis_title='Anzahl der Straftaten',
    plot_bgcolor='white',  # Transparenter Hintergrund
    paper_bgcolor='white',  # Transparenter Hintergrund
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=1, label="1M", step="month", stepmode="backward"),
                dict(count=6, label="6M", step="month", stepmode="backward"),
                dict(count=1, label="YTD", step="year", stepmode="todate"),
                dict(count=1, label="1Y", step="year", stepmode="backward"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(visible=True),
        type="date"
    )
)

# Diagramm anzeigen
fig.show()

## Verlauf der Straftaten über die Zeit, Tagesansicht
Um Trends im Tagesverlauf zu erkennen, bietet es sich an, einen Blick auf die einzelnen Tage während des Beobachtungszeitraums zu werfen. Das Diagramm stellt jeden Tag als einzelne Säule im Säulendiagramm dar. Betrachtet man die Säulen, fällt auf, dass besonders am 1. Tag eines jeden Monats auffällig viele Straftaten dokumentiert wurden. Während der Datenrecherche kam die Vermutung auf, dass dies möglicherweise darauf zurückzuführen ist, dass Verbrechen, die erst nach vielen Tagen gemeldet wurden, auf den 1. Tag des Monats dokumentiert werden könnten, da der genaue Tatzeitpunkt nur grob geschätzt werden kann.

In [27]:
# Datumsformat korrigieren und Datum extrahieren
df['date_occurrence'] = pd.to_datetime(df['DATE OCC'], format='%m/%d/%Y %I:%M:%S %p')

# Tägliche Aggregation vorbereiten
df['day'] = df['date_occurrence'].dt.date
daily_crimes = df.groupby('day').size().reset_index(name='counts')
daily_crimes['day'] = pd.to_datetime(daily_crimes['day'])

# Erstellung Säulendiagramm
fig = px.bar(daily_crimes, x='day', y='counts',
             title='Entwicklung der Straftaten in Los Angeles',
             labels={'counts': 'Anzahl der Straftaten', 'day': 'Datum'},
             template='plotly_white')

# Anpassung Layout
fig.update_layout(
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=7, label="Woche", step="day", stepmode="backward"),
                dict(count=1, label="Monat", step="month", stepmode="backward"),
                dict(count=6, label="6M", step="month", stepmode="backward"),
                dict(count=1, label="YTD", step="year", stepmode="todate"),
                dict(step="all")
            ])
        ),
        rangeslider=dict(visible=True),
        type="date"
    ),
    yaxis=dict(title='Anzahl der Straftaten'),
    xaxis_title='Datum',
)

# Auswahl der täglichen Daten
def update_graph(step):
    if step in ['Woche', 'Monat']:
        # Tägliche Daten verwenden
        fig.data = []
        fig.add_bar(x=daily_crimes['day'], y=daily_crimes['counts'])
        fig.layout.xaxis.dtick = "D1"  # Tägliche Ticks

    fig.show()

# Diagramm anzeigen
fig.show()

## Durchschnittliche Verzögerung bei der Meldung der Straftaten nach Tag des Monats
Um diese Vermutung zu überprüfen, zeigt das folgende Diagramm die durchschnittliche Verzögerung bei der Meldung von Straftaten. Auffällig ist, dass die Verzögerung am 1. Tag des Monats im Durchschnitt etwa 6 Mal höher ist als an den anderen Tagen, was die Vermutung bestätigen könnte.

In [28]:
df_cln['date_rptd'] = pd.to_datetime(df_cln['date_rptd'], format='%m/%d/%Y %I:%M:%S %p')
df_cln['date_occurance'] = pd.to_datetime(df_cln['date_occurance'], format='%m/%d/%Y %I:%M:%S %p')

# Berechnung der Verzögerung in Tagen
df_cln['report_delay'] = (df_cln['date_rptd'] - df_cln['date_occurance']).dt.days

# Gruppierung nach dem Tag des Monats der Begebenheit
report_delay_summary = df_cln.groupby(df_cln['date_occurance'].dt.day)['report_delay'].mean().reset_index()
report_delay_summary.columns = ['Tag des Monats', 'Durchschnittliche Verzögerung in Tagen']

# Erstellung des Balkendiagramms
fig = px.bar(report_delay_summary, x='Tag des Monats', y='Durchschnittliche Verzögerung in Tagen',
             title='Durchschnittliche Verzögerung bei der Meldung nach Tag des Monats',
             labels={'Tag des Monats': 'Tag des Monats', 'Durchschnittliche Verzögerung in Tagen': 'Durchschnittliche Verzögerung (Tage)'},
             template='plotly_white')

# Anpassungen Layout
fig.update_layout(
    plot_bgcolor='white',
    paper_bgcolor='white',
    font=dict(color='black')
)

# Diagramm anzeigen
fig.show()

## Prozentuale Aufteilung der Straftaten, die erst nach mehr als 100 Tagen gemeldet worden sind, auf die Monate
Dieses Diagramm betrifft ausschließlich Straftaten, die erst nach mehr als 100 Tagen gemeldet wurden. Auch hier fällt auf, dass mehr als ein Viertel dieser Straftaten auf den 1. des Monats datiert sind. Im Vergleich dazu machen alle anderen Tage nur etwa 2-4% dieser Straftaten aus. Dies lässt vermuten, dass die "fehlerhafte" Erfassung der Daten wahrscheinlich die Ursache für die Ausschläge zum Monatsanfang ist. Daher bestätigt dieses Diagramm die Vermutung, dass Straftaten, die erst sehr viel später gemeldet wurden, überdurchschnittlich oft auf den Monatsanfang zurückdatiert wurden.

In [29]:
# Sicherstellung der Umwandlung der Datumsformate
df_cln['date_rptd'] = pd.to_datetime(df_cln['date_rptd'], format='%m/%d/%Y %I:%M:%S %p')
df_cln['date_occurance'] = pd.to_datetime(df_cln['date_occurance'], format='%m/%d/%Y %I:%M:%S %p')

# Berechnung der Verzögerung in Tagen
df_cln['report_delay'] = (df_cln['date_rptd'] - df_cln['date_occurance']).dt.days

# Filtern der Daten => Verzögerung mehr als 100 Tage
long_delay_crimes = df_cln[df_cln['report_delay'] > 100]

# Gruppieren nach dem Tag des Monats des Auftretens
long_delay_summary = long_delay_crimes['date_occurance'].dt.day.value_counts().reset_index()
long_delay_summary.columns = ['Day of Month', 'Count']

vivid_colors = px.colors.qualitative.Set3

# Erstellung Kuchendiagramm
fig = px.pie(long_delay_summary, values='Count', names='Day of Month',
             title='Verteilung der lang verzögerten Straftatmeldungen nach Tag des Monats',
             color_discrete_sequence=vivid_colors)

fig.update_layout(plot_bgcolor='white', paper_bgcolor='white', font=dict(color='black'))

# Diagramm anzeigen
fig.show()

## Interaktive Karte von Los Angeles (langzeit)
Nun wird untersucht, wie sich die Straftaten in Los Angeles langfristig entwickelt haben. Das Diagramm nutzt die Geodaten, die im Datensatz für alle dokumentierten Straftaten gespeichert sind. Dabei zeigt sich, dass Downtown Los Angeles sowie der Stadtteil Hollywood als Schauplätze für besonders viele Straftaten auf engem Raum gelten. An einigen Stellen in der Grafik ist zu erkennen, dass sich das Verbrechen ab Mitte bis Ende 2022 auch etwas in die Gebiete westlich und östlich des Zentrums ausgedehnt hat.

In [40]:
df_cln['date_occurance'] = pd.to_datetime(df_cln['date_occurance'])
df_cln['month_year'] = df_cln['date_occurance'].dt.strftime('%Y-%m')

# Aggregieren der Daten
crime_data_monthly = df_cln.groupby(['month_year', 'area_name', 'LAT', 'LON']).size().reset_index(name='counts')

# Farbanpassung
darker_blue_scale = [
    (0.0, 'rgba(0, 76, 153, 1)'),
    (1.0, 'rgba(0, 38, 77, 1)')
]

# Skalierung der "counts" => Einfluss auf Größe der Kreise
max_size = 15
crime_data_monthly['scaled_size'] = (crime_data_monthly['counts'] / 250) * max_size

# Karte erstellen
fig = px.scatter_mapbox(crime_data_monthly, lat='LAT', lon='LON', color='counts',
                        size='scaled_size', hover_name='area_name', hover_data=['counts'],
                        color_continuous_scale=darker_blue_scale,
                        animation_frame='month_year', mapbox_style='carto-positron',
                        range_color=[0, 250])  # Setzt den Farbbereich konstant von 0 bis 250

# Layout anpassen
fig.update_layout(
    title='Monatliche Entwicklung der Kriminalität in Los Angeles nach Bezirk',
    margin={'r':0, 't':0, 'l':0, 'b':0},
    mapbox=dict(center=dict(lat=34.0522, lon=-118.2437), zoom=10),
    paper_bgcolor='white',
    plot_bgcolor='white',
    font=dict(color='black')
)

# Konfiguration des Animationsschiebereglers
fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 500
fig.layout.sliders[0].currentvalue.prefix = 'Monat: '

# Diagramm anzeigen
fig.show()

Output hidden; open in https://colab.research.google.com to view.

## Entwicklung der Anzahl der Straftaten in den einzelnen Bezirken (langzeit)
Um die Verteilung der Straftaten auf die einzelnen Bezirke während dieser Zeit zu verdeutlichen, zeigt die nächste Grafik die langfristige Entwicklung der Straftaten pro Bezirk. Auch hier wird ersichtlich, dass sich ein überdurchschnittlich hoher Anteil an Straftaten in den Bezirken 77th Street und Central abspielt.

In [31]:
df_cln['date_occurance'] = pd.to_datetime(df_cln['date_occurance'])
df_cln['month_year'] = df_cln['date_occurance'].dt.strftime('%Y-%m')

# Aggregieren der Daten nach Bezirk und Monat
crime_data_monthly = df_cln.groupby(['month_year', 'area_name']).size().reset_index(name='counts')

# Liste der Bezirke => Reihenfolge konstant machen, damit die Übersicht besser wird.
area_list = sorted(df_cln['area_name'].unique())

# Erstellung Säulendiagramm und Animation
fig = px.bar(crime_data_monthly, x='area_name', y='counts', color='counts',
             animation_frame='month_year',
             category_orders={"area_name": area_list},  # Konstante Reihenfolge der Bezirke
             labels={'area_name': 'Bezirk', 'counts': 'Anzahl der Straftaten'},
             title='Monatliche Entwicklung der Kriminalität in Los Angeles nach Bezirk',
             color_continuous_scale=px.colors.sequential.Blues)  # Blaue Farbskala

# Anpassung Layout
fig.update_layout(
    xaxis={'categoryorder': 'array', 'categoryarray': area_list},  # Konstante Reihenfolge der x-Achse
    yaxis=dict(title='Anzahl der Straftaten', range=[0, 1750]),  # Festlegen der y-Achse Skala
    xaxis_title='Bezirk',
    plot_bgcolor='white',
    paper_bgcolor='white',
    font=dict(color='black')  # Schwarze Schrift für bessere Lesbarkeit
)

# zweite y-Achse entfernen, da eine dynamische y-Achse keine gute Visualisierung ermöglicht
if 'yaxis2' in fig.layout:
    del fig.layout['yaxis2']

# Konfiguration des Animationsschiebereglers
fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 500
fig.layout.sliders[0].currentvalue.prefix = 'Monat: '




fig = px.bar(crime_data_monthly, x='area_name', y='counts',
             animation_frame='month_year', labels={'counts': 'Anzahl der Straftaten'})

# zweite y-Achse entfernen, da eine dynamische y-Achse keine gute Visualisierung ermöglicht
if 'yaxis2' in fig.layout:
    del fig.layout['yaxis2']

fig.update_layout(
    xaxis={'categoryorder': 'array', 'categoryarray': area_list, 'title': 'Bezirk'},  # Anpassen der x-Achsen-Beschriftung
    yaxis=dict(title='Anzahl der Straftaten', range=[0, 1750]),  # Festlegen der y-Achse Skala
    plot_bgcolor='white',  # Weißer Hintergrund
    paper_bgcolor='white',  # Weißer Hintergrund des Papiers
    font=dict(color='black')  # Schwarze Schrift für bessere Lesbarkeit
)

fig.layout.sliders[0].currentvalue.prefix = 'Monat: '
fig.update_layout(yaxis=dict(range=[0, 1750]))

# Diagramm anzeigen
fig.show()

## Interaktive Karte von Los Angeles (tageszeitabhängig)
Neben der Analyse der Langzeitentwicklung spielt auch die Untersuchung der Uhrzeiten, zu denen Straftaten aufgetreten sind, eine große Rolle. Aus diesem Grund zeigt dieses Diagramm, zu welcher Uhrzeit es an welchen Orten zu Straftaten kam. Hier lässt sich erkennen, dass die Straftaten zwischen Mitternacht und 5 Uhr abnehmen, dann ansteigen und tagsüber um 12 und 17 Uhr am häufigsten vorkommen.

In [32]:
df_cln['time_occurance'] = df_cln['time_occurance'].astype(str).str.zfill(4)  # Stellen sicher, dass alle Zeiten vierstellig sind
df_cln['hour'] = df_cln['time_occurance'].str[:2] + ':00'  # Stunde extrahieren und als 'hh:00' formatieren

# Aggregieren der Daten nach Stunden und Bezirken
crime_data_hourly = df_cln.groupby(['hour', 'area', 'LAT', 'LON']).size().reset_index(name='counts')

# Farben anpassen => zur Unterscheidung zu anderem Diagramm
red_scale = [
    (0.0, 'rgba(255, 99, 71, 0.5)'),
    (1.0, 'rgba(139, 0, 0, 1)')
]

# Skalierung der "counts" => Einfluss auf Größe der Kreise
max_size = 15
crime_data_hourly['scaled_size'] = (crime_data_hourly['counts'] / crime_data_hourly['counts'].max()) * max_size

# Karte erstellen
fig = px.scatter_mapbox(crime_data_hourly, lat='LAT', lon='LON', color='counts',
                        size='scaled_size', hover_name='area', hover_data=['counts'],
                        color_continuous_scale=red_scale,
                        animation_frame='hour', mapbox_style='carto-positron',
                        range_color=[0, 200])

# Anpassung Layout
fig.update_layout(
    title='Stündliche Entwicklung der Kriminalität in Los Angeles nach Bezirk',
    margin={'r':0, 't':0, 'l':0, 'b':0},
    mapbox=dict(center=dict(lat=34.0522, lon=-118.2437), zoom=10),
    paper_bgcolor='white',
    plot_bgcolor='white',
    font=dict(color='black')
)

# Konfiguration des Animationsschiebereglers
fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 500  # Schnellere Übergänge zwischen Stunden
fig.layout.sliders[0].currentvalue.prefix = 'Zeit: '

# Diagramm anzeigen
fig.show()

Output hidden; open in https://colab.research.google.com to view.

## Entwicklung der Anzahl der Straftaten in den einzelnen Bezirken (tageszeitabhängig)
Im Folgenden wird die stündliche Entwicklung der Straftaten in den einzelnen Bezirken untersucht. Auch hier lässt sich erkennen, dass in den Bezirken Central und 77th Street sowie Pacific generell eine höhere Kriminalitätsrate vorliegt als in allen anderen Bezirken.

In [33]:
df_cln['time_occurance'] = df_cln['time_occurance'].astype(str).str.zfill(4)  # Stellen sicher, dass alle Zeiten vierstellig sind
df_cln['hour'] = df_cln['time_occurance'].str[:2] + ':00'  # Stunde extrahieren und als 'hh:00' formatieren

# Aggregieren der Daten nach Stunden und Bezirken
crime_data_hourly = df_cln.groupby(['hour', 'area_name']).size().reset_index(name='counts')

# Liste der Bezirke für konstante Reihenfolge => zur besseren Übersicht/Visualisierung
area_list = sorted(df_cln['area_name'].unique())

# Erstellung Säulendiagramm + Animation
fig = px.bar(crime_data_hourly, x='area_name', y='counts',
             animation_frame='hour',
             category_orders={"area_name": area_list},  # Konstante Reihenfolge der Bezirke
             labels={'area_name': 'Bezirk', 'counts': 'Anzahl der Straftaten'},
             title='Stündliche Entwicklung der Kriminalität in Los Angeles nach Bezirk',
             color_discrete_sequence=['orange'])  # Einheitliche Farbe

# Anpassung Layout
fig.update_layout(
    xaxis={'categoryorder': 'array', 'categoryarray': area_list},  # Konstante Reihenfolge der x-Achse
    yaxis=dict(title='Anzahl der Straftaten', range=[0, 4600]),  # Konstante y-Achse Skala
    xaxis_title='Bezirk',
    plot_bgcolor='white',
    paper_bgcolor='white',
    font=dict(color='black')  # Schwarze Schrift für bessere Lesbarkeit
)

# Konfiguration des Animationsschiebereglers
fig.layout.updatemenus[0].buttons[0].args[1]['frame']['duration'] = 500
fig.layout.sliders[0].currentvalue.prefix = 'Stunde: '

# Diagramm anzeigen
fig.show()

## Histogramm in Bezug auf Alter und Geschlecht der Opfer
Die Analyse der Opfer zeigt, dass ein Großteil der Opfer zwischen 24 und 34 Jahren alt ist. Zudem lässt sich erkennen, dass ältere Menschen deutlich seltener Opfer von Verbrechen werden. Es fällt allerdings auf, dass bis zum Alter von 33 Jahren eher Frauen Opfer von Verbrechen werden, während ab diesem Alter dieses Verhältnis kippt und mehr Männer Opfer werden.

In [34]:
df_cln = df_cln[df_cln['victim_age'] > 0]  # Annahme: Entfernen von ungültigen Altersangaben
df_cln = df_cln[df_cln['victim_sex'].isin(['M', 'F', 'X'])]  # Einschließen von 'M', 'F' und 'X'

# Erstellen eines Gruppen-Histogramms
fig = px.histogram(df_cln, x='victim_age', color='victim_sex',
                   barmode='group',
                   nbins=50,  # Anzahl der Bins anpassen für detailliertere Darstellung
                   title='Verteilung der Opfer nach Alter und Geschlecht',
                   labels={'victim_age': 'Alter der Opfer', 'victim_sex': 'Geschlecht der Opfer'},
                   color_discrete_map={'M': '#027cf5', 'F': '#f58402', 'X': 'grey'}  # Farben für Geschlechter, inklusive 'X'
                  )

# Anpassung Layout
fig.update_layout(
    xaxis_title='Alter',
    yaxis_title='Anzahl der Opfer',
    plot_bgcolor='white',
    paper_bgcolor='white',
    font=dict(color='black')
)

# Diagramm anzeigen
fig.show()

## Histogramm in Bezug auf Herkunft und Alter der Opfer
Die Verteilung der Herkunft der Opfer zeigt, dass eine große Anzahl der Opfer lateinamerikanischer Herkunft sind, gefolgt von Menschen mit europäischer und afroamerikanischer Herkunft. Dies entspricht auch der allgemeinen Bevölkerungsstruktur, da etwa die Hälfte aller Menschen in Los Angeles lateinamerikanischer Herkunft ist. Zudem fällt auf, dass bei den älteren Menschen ab einem Alter von etwa 58 Jahren häufiger weiße Menschen Opfer von Straftaten werden.

In [35]:
df_cln = df_cln[df_cln['victim_age'] > 0]  # Annahme: Entfernen von ungültigen Altersangaben
df_cln = df_cln[df_cln['victim_descent'].isin(['W', 'B', 'H', 'A', 'O'])]  # Einschließen der spezifizierten Herkunftsgruppen

# Zuordnungstabelle für die Abkürzungen
descent_mapping = {'W': 'Weiß', 'B': 'Schwarz', 'H': 'Hispanic', 'A': 'Asiatisch', 'O': 'Andere'}
df_cln['victim_descent'] = df_cln['victim_descent'].map(descent_mapping)  # Ersetze Abkürzungen durch volle Namen

# Erstellen eines Gruppen-Histogramms
fig = px.histogram(df_cln, x='victim_age', color='victim_descent',
                   barmode='group',
                   nbins=50,  # Anzahl der Bins anpassen für detailliertere Darstellung
                   title='Verteilung der Opfer nach Alter und Herkunft',
                   labels={'victim_age': 'Alter der Opfer', 'victim_descent': 'Herkunft der Opfer'},
                   color_discrete_map={
                       'Weiß': 'blue',
                       'Schwarz': 'black',
                       'Hispanic': 'brown',
                       'Asiatisch': 'green',
                       'Andere': 'grey'
                   }
                  )

# Anpassungen Layout
fig.update_layout(
    xaxis_title='Alter',
    yaxis_title='Anzahl der Opfer',
    plot_bgcolor='white',
    paper_bgcolor='white',
    font=dict(color='black')
)

# Diagramm anzeigen
fig.show()

## Anteil der verscheidenen Straftaten
Im Folgenden wird die prozentuale Verteilung der Straftaten analysiert. Es zeigt sich, dass die meisten Straftaten die Bezeichnung "BATTERY - SIMPLE ASSAULT" tragen, was auf eine einfache Körperverletzung oder einen Angriff hinweist. Danach folgen Delikte des Identitätsdiebstahls, Fahrzeugdiebstähle sowie schwere Körperverletzungen und weitere Vergehen.

In [36]:
crime_counts = df_cln['crm_code_desc'].value_counts().reset_index()
crime_counts.columns = ['Crime Type', 'Counts']

# Berechnung des Gesamtanteils jeder Straftat
total_crimes = crime_counts['Counts'].sum()
crime_counts['Percentage'] = 100 * crime_counts['Counts'] / total_crimes

# Zusammenfassung von Straftaten mit geringem Gesamtanteil
threshold = 2.5
small_crimes = crime_counts[crime_counts['Percentage'] < threshold]
other_sum = small_crimes['Counts'].sum()

# Entfernen kleiner Kategorien und Hinzufügen der "Other" Kategorie
crime_counts = crime_counts[crime_counts['Percentage'] >= threshold]
other_row = pd.DataFrame({'Crime Type': ['Other'], 'Counts': [other_sum], 'Percentage': [sum(small_crimes['Percentage'])]})
crime_counts = pd.concat([crime_counts, other_row], ignore_index=True)

# Erstellung Kreisdiagramm
fig = px.pie(crime_counts, values='Counts', names='Crime Type', title='Verteilung der Straftaten')
fig.update_layout(
    plot_bgcolor='white',  # Weißer Hintergrund
    paper_bgcolor='white',  # Weißer Hintergrund des Papiers
    font=dict(color='black', size=12)  # Schwarze Schrift
)

# Diagramm anzeigen
fig.show()

## Anteil der verschiedenen verwendeten Waffen
Von den etwa 650.000 analysierten Delikten wurde bei etwa 40% der Fälle eine Waffe verwendet. Dabei wird ersichtlich, dass in einem sehr großen Anteil der Fälle der eigene Körper des Angreifers als Waffe genutzt wurde, gefolgt von Waffen, die den Ermittlern nicht genau bekannt sind, und verbalen Drohungen. Handfeuerwaffen, Messer oder automatische Waffen wurden eher seltener verwendet.

In [37]:
weapon_counts = df_cln['weapon_desc'].value_counts().reset_index()
weapon_counts.columns = ['Weapon', 'Counts']

# Sortieren der Waffen nach Häufigkeit + Auswahl der Top 10
top_weapons = weapon_counts.head(10)
other_weapons = weapon_counts.iloc[10:]
other_sum = pd.DataFrame({'Weapon': ['Other'], 'Counts': [other_weapons['Counts'].sum()]})

# Zusammenführen der Top 10 Waffen und der "Other"-Kategorie
final_data = pd.concat([top_weapons, other_sum])

# Erstellung Balkendiagramm
fig = px.bar(final_data, x='Weapon', y='Counts', title='Häufigkeit der verwendeten Waffen bei Straftaten',
             color='Counts', color_continuous_scale=px.colors.sequential.Blues)

# Anpassungen Layout
fig.update_layout(
    plot_bgcolor='white',
    paper_bgcolor='white',
    font=dict(color='black'),
    xaxis_title="Waffe",
    yaxis_title="Anzahl der Vorfälle"
)

# Diagramm anzeigen
fig.show()

Die Analyse der Straftaten in Los Angeles bietet einige wichtige Erkenntnisse. Einerseits zeigt die Analyse, dass es wichtig ist, die Daten korrekt zu interpretieren, um Missverständnisse, wie beispielsweise durch die Datierung vieler Straftaten auf den 1. des Monats, zu vermeiden. Darüber hinaus gibt es verschiedene Anspruchsgruppen, die ein Interesse an der korrekten Erhebung und Interpretation der Daten haben können:

Die Öffentlichkeit, z.B. Bürgermeister, Gemeinden, etc.: Sie benötigen Einblicke in gesellschaftliche Verhältnisse und Entwicklungen, um Sicherheitsmaßnahmen und Präventionsstrategien gezielt zu gestalten und das Vertrauen in die Gemeinschaft zu stärken. Eine Kriminalitätsstatistik bietet ihnen solche Einblicke.

Polizei oder Sicherheitspersonal: Die Polizei oder das Sicherheitspersonal benötigt genaue Daten zur effektiven Planung von Verbrechensbekämpfungsmaßnahmen, Ressourcenallokation und proaktiven Maßnahmen zur Verhinderung von Straftaten.

Versicherungen: Versicherungsunternehmen nutzen interpretierte Daten zur Bewertung von Risiken und zur Schadensprävention, um angemessene Prämien festzulegen und geeignete Schutzmaßnahmen zu empfehlen.

Bürger, Urlauber, etc.: Als Bewohner von Los Angeles oder auch als Tourist kann es sinnvoll sein, Gebiete und Zeiten, in denen potenziell viele Straftaten begangen werden, zu kennen.

## Textquellen:
1) https://www.travellersarchive.de/hollywood-filmstudios/#:~:text=Es%20gibt%20etliche%20Filmstudios%20in,Paramount%20Pictures%20und%20Sony%20Pictures

2) https://mayor.lacity.gov/news/lapd-releases-end-year-crime-statistics-city-los-angeles-2023

3) https://www.planet-wissen.de/kultur/metropolen/los_angeles_stadt_der_engel/index.html#:~:text=Die%20gr%C3%B6%C3%9Fte%20Bev%C3%B6lkerungsgruppe%20sind%20die,aus%20allen%20Teilen%20der%20Erde

## Datenquellen:
1) https://www.kaggle.com/datasets/sumaiaparveenshupti/los-angeles-crime-data-20102020?resource=download